In [1]:
library(forecast)
library(M4comp2018)
library(dplyr)

Registered S3 method overwritten by 'quantmod':
  method            from
  as.zoo.data.frame zoo 


Attaching package: ‘dplyr’


The following objects are masked from ‘package:stats’:

    filter, lag


The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union




In [2]:
etsl=load('Quarterly_ets_datalist.RData')
ets_datalist <- eval(parse(text = etsl))
thetafl=load('Quarterly_thetaf_datalist.RData')
thetaf_datalist <- eval(parse(text = thetafl))

In [3]:
ets_predh=ets_datalist[[2]]
thetaf_predh=thetaf_datalist[[2]]

In [4]:
ets_pred_res=ets_datalist[[1]]
thetaf_pred_res=thetaf_datalist[[1]]

In [5]:
etsoptl=load('Quarterly_ets_opt_pre_result.RData')
ets_opt_pre_list<- eval(parse(text = etsoptl))
thetafoptl=load('Quarterly_thetaf_opt_pre_result.RData')
thetaf_opt_pre_list<- eval(parse(text = thetafoptl))

In [6]:
time_matrix <- matrix(0,ncol = 3, nrow =3)
colnames(time_matrix) <- c("user_time", "system_time", "elapsed_time")
start_time = Sys.time()

In [7]:
ets_pr_min=ets_opt_pre_list[[1]]
ets_pr_mean=ets_opt_pre_list[[2]]
thetaf_pr_min=thetaf_opt_pre_list[[1]]
thetaf_pr_mean=thetaf_opt_pre_list[[2]]

In [8]:
head(ets_pr_min)

xgbclsmin xgbregmin lgbclsmin lgbregmin
[1,] 1         1.1559789 4         1.515028 
[2,] 2         1.8558538 3         1.654567 
[3,] 2         1.7886213 4         1.828702 
[4,] 2         1.8101646 0         1.878932 
[5,] 0         0.8557799 0         1.090760 
[6,] 0         2.5231853 4         2.249279

In [9]:
ets_pr_min=ets_pr_min+1
ets_pr_mean=ets_pr_mean+1
thetaf_pr_min=thetaf_pr_min+1
thetaf_pr_mean=thetaf_pr_mean+1


In [10]:
head(ets_pr_min)

xgbclsmin xgbregmin lgbclsmin lgbregmin
[1,] 2         2.155979  5         2.515028 
[2,] 3         2.855854  4         2.654567 
[3,] 3         2.788621  5         2.828702 
[4,] 3         2.810165  1         2.878932 
[5,] 1         1.855780  1         2.090760 
[6,] 1         3.523185  5         3.249279

In [11]:
round5=function(x)
    {
    l=round(x)
    for(i in 1:length(l))
    {
    if(l[i]>5)
        {
        l[i]=5
    }
    if(l[i]<1)
    {
        l[i]=1
    }
}
    return(l)
}

In [12]:
ets_pr_min[,2]=round5(ets_pr_min[,2])
ets_pr_min[,4]=round5(ets_pr_min[,4])

In [13]:
ets_pr_mean[,2]=round5(ets_pr_mean[,2])
ets_pr_mean[,4]=round5(ets_pr_mean[,4])

In [14]:
thetaf_pr_min[,2]=round5(thetaf_pr_min[,2])
thetaf_pr_min[,4]=round5(thetaf_pr_min[,4])

In [15]:
thetaf_pr_mean[,2]=round5(thetaf_pr_mean[,2])
thetaf_pr_mean[,4]=round5(thetaf_pr_mean[,4])

In [16]:
head(ets_pr_min)

xgbclsmin xgbregmin lgbclsmin lgbregmin
[1,] 2         2         5         3        
[2,] 3         3         4         3        
[3,] 3         3         5         3        
[4,] 3         3         1         3        
[5,] 1         2         1         2        
[6,] 1         4         5         3

In [17]:
Quarterly_M4 <- Filter(function(l) l$period == "Quarterly", M4)

In [18]:
data=Quarterly_M4

In [19]:
datalength=length(data)
h=data[[1]]$h
m=10
n=4
freq=frequency(data[[1]]$x)

In [20]:
realxx=matrix(0,datalength,h)
for(i in 1:datalength){
    realxx[i,]=data[[i]]$xx
}

In [21]:
length5=matrix(0,datalength,m)
for(k in 1:datalength)
{
y = data[[k]]$x
y_l=length(y)
loc = 1:length(y)
loc_m = as.integer(loc*m/length(y))
filt_d = data.frame(y,loc_m)
filt_0=filter(filt_d ,loc_m==0)
m_l=count(filt_0)
m_l=as.integer(m_l)
length5[k,]=c(0,1*m_l,2*m_l,3*m_l,4*m_l)
    }

In [22]:
end_time = Sys.time()
time_matrix[1,]=end_time-start_time

In [23]:
end_time-start_time

Time difference of 1.44938 mins

## ETS

In [24]:
start_time = Sys.time()

In [25]:
set.seed(100)
index = sample(2,length(data),replace = TRUE,prob=c(0.7,0.3))
testindex=c(1:length(data))[index==2]

In [26]:
meanpre=function(pred_array,opt_pr,h,testindex)
    {
    data_length=length(testindex)
    meanpreh=matrix(0,data_length,h)
    for (i in 1:data_length){
    index=testindex[i]
    loc=opt_pr[index]
    predh=pred_array[index,loc,,]
    predh=unique(predh)
    meanpreh[i,]=apply(predh,2,mean)
}
    return(meanpreh)
}

In [27]:
predres=function(pred_matrix,data,opt_pr,lengthmatrix,h,testindex)
    {
    data_length=length(testindex)
    pred_res=matrix(0,data_length,6)
    model=ets(data[[1]]$x)
    fore_l=forecast(model,h=h)
    freq=frequency(data[[1]]$x)
    for (i in 1:data_length){
    index=testindex[i]
    loc=opt_pr[index]
    start=lengthmatrix[i,loc]
    y_all=data[[index]]$x
    y=y_all[start:length(y_all)]
    fore_l$x=ts(y,frequency=freq,end=end(y_all))
    real=data[[index]]$xx
    fore_l$mean=ts(pred_matrix[i,],start=start(real),frequency=freq)
    res=accuracy(fore_l,real)
    pred_res[i,]=res[2,1:6]
    }
    return(pred_res)
    }

In [28]:
predres_mul=function(pred_matrix,data,opt_pr_mul,lengthmatrix,h,testindex)
    {
    data_length=length(testindex)
    pred_res=matrix(0,data_length,6)
    model=ets(data[[1]]$x)
    fore_l=forecast(model,h=h)
    freq=frequency(data[[1]]$x)
    for (i in 1:data_length){
    index=testindex[i]
    loc=min(opt_pr_mul[index,])
    start=lengthmatrix[i,loc]
    y_all=data[[index]]$x
    y=y_all[start:length(y_all)]
    fore_l$x=ts(y,frequency=freq,end=end(y_all))
    real=data[[index]]$xx
    fore_l$mean=ts(pred_matrix[i,],start=start(real),frequency=freq)
    res=accuracy(fore_l,real)
    pred_res[i,]=res[2,1:6]
    }
    return(pred_res)
    }

In [29]:
etsxgbcls_min=meanpre(ets_predh,ets_pr_min[,1],h,testindex)
etsxgbreg_min=meanpre(ets_predh,ets_pr_min[,2],h,testindex)
etslgbcls_min=meanpre(ets_predh,ets_pr_min[,3],h,testindex)
etslgbreg_min=meanpre(ets_predh,ets_pr_min[,4],h,testindex)

In [30]:
etsxgbcls_mean=meanpre(ets_predh,ets_pr_mean[,1],h,testindex)
etsxgbreg_mean=meanpre(ets_predh,ets_pr_mean[,2],h,testindex)
etslgbcls_mean=meanpre(ets_predh,ets_pr_mean[,3],h,testindex)
etslgbreg_mean=meanpre(ets_predh,ets_pr_mean[,4],h,testindex)

### The error of each improved prediction result

In [31]:
lengthtest=length5[testindex,]

In [32]:
etsminxgbclsres=predres(etsxgbcls_min,data,ets_pr_min[,1],lengthtest,h,testindex)
etsminxgbregres=predres(etsxgbreg_min,data,ets_pr_min[,2],lengthtest,h,testindex)
etsminlgbclsres=predres(etslgbcls_min,data,ets_pr_min[,3],lengthtest,h,testindex)
etsminlgbregres=predres(etslgbreg_min,data,ets_pr_min[,4],lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

In [33]:
etsmeanxgbclsres=predres(etsxgbcls_mean,data,ets_pr_mean[,1],lengthtest,h,testindex)
etsmeanxgbregres=predres(etsxgbreg_mean,data,ets_pr_mean[,2],lengthtest,h,testindex)
etsmeanlgbclsres=predres(etslgbcls_mean,data,ets_pr_mean[,3],lengthtest,h,testindex)
etsmeanlgbregres=predres(etslgbreg_mean,data,ets_pr_mean[,4],lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

In [34]:
end_time = Sys.time()
time_matrix[2,]=end_time-start_time

### The results of the two methods of determining labels are averaged respectively

In [35]:
etsallmin=(etsxgbcls_min+etslgbcls_min+etsxgbreg_min+etslgbreg_min)/4
etsallmean=(etsxgbcls_mean+etslgbcls_mean+etsxgbreg_mean+etslgbreg_mean)/4

In [36]:
etsallminres=predres_mul(etsallmin,data,ets_pr_min,lengthtest,h,testindex)
etsallmeanres=predres_mul(etsallmean,data,ets_pr_mean,lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

### Under the above classification, the improved forecast results of the classification and regression models are averaged respectively

In [37]:
etsclsmin=(etsxgbcls_min+etslgbcls_min)/2
etsregmin=(etsxgbreg_min+etslgbreg_min)/2
etsclsmean=(etsxgbcls_mean+etslgbcls_mean)/2
etsregmean=(etsxgbreg_mean+etslgbreg_mean)/2

In [38]:
etsclsminres=predres_mul(etsclsmin,data,ets_pr_min[,c(1,3)],lengthtest,h,testindex)
etsregminres=predres_mul(etsregmin,data,ets_pr_min[,c(2,4)],lengthtest,h,testindex)
etsclsmeanres=predres_mul(etsclsmean,data,ets_pr_mean[,c(1,3)],lengthtest,h,testindex)
etsregmeanres=predres_mul(etsregmean,data,ets_pr_mean[,c(2,4)],lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

### Random slice

In [39]:
etspred_change<- aperm(ets_predh[1:datalength,1:m,1:n,1:h], c(1, 3, 2, 4))  
# 使用array函数将其转换为新的形状
etspred_change <- array(etspred_change, dim = c(datalength, m*n, h))

In [40]:
model=ets(data[[1]]$x)
fore_l=forecast(model,h=h)
etsrandomres=matrix(0,datalength,6)
for (i in 1:datalength){
    random=sample(m*n,n)
    minloc=min(random)
    # 使用cut函数将数据分割为区间
    loc <- cut(minloc, breaks =seq(0,m*n,n), labels = FALSE)
    loc<-as.numeric(loc)
    etsrandompred=apply(etspred_change[i,random,],2,mean)
    start=length5[i,loc]
    y_all=data[[i]]$x
    y=y_all[start:length(y_all)]
    fore_l$x=ts(y,frequency=freq,end=end(y_all))
    real=data[[i]]$xx
    fore_l$mean=ts(etsrandompred,start=start(real),frequency=freq)
    res=accuracy(fore_l,real)
    etsrandomres[i,]=res[2,1:6]
    }

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

In [41]:
mean1=function(x)
    {
# 使用is.finite函数检查哪些值是有限的
finite_values <- x[is.finite(x)]
# 计算有限值的平均值
d=mean(finite_values, na.rm = TRUE)
return(d)
}

In [42]:
print(apply(ets_pred_res[testindex,1,1,],2,mean1))
print(apply(etsminxgbclsres,2,mean1))
print(apply(etsminxgbregres,2,mean1))
print(apply(etsminlgbclsres,2,mean1))
print(apply(etsminlgbregres,2,mean1))

[1]   9.762626 691.840789 586.851015  -3.008543  12.195383   1.153780
[1]  63.3255161 680.6060372 578.5390133  -2.1751344  11.8156361   0.9870874
[1]  65.5720454 689.4226714 585.7298847  -1.9844577  11.9624407   0.9851388
[1]  55.126979 690.372063 586.132538  -2.025560  11.979606   1.100278
[1]  53.5887584 686.6011046 582.3818755  -2.0210214  11.9358043   0.9770844


In [43]:
print(apply(etsmeanxgbclsres,2,mean1))
print(apply(etsmeanxgbregres,2,mean1))
print(apply(etsmeanlgbclsres,2,mean1))
print(apply(etsmeanlgbregres,2,mean1))

[1]  53.4468921 675.4016966 571.8115921  -2.2684573  11.7286929   0.9633273
[1]  45.2449408 681.8849624 578.1710258  -2.3124757  11.7841974   0.9704909
[1]  50.679873 692.557652 588.746771  -2.232859  12.034242   1.107010
[1]  36.1235753 688.5117588 584.2672418  -2.2236928  11.9552557   0.9857779


In [44]:
print(apply(etsallminres,2,mean1))
print(apply(etsallmeanres,2,mean1))

[1]  59.403325 673.625467 571.488026  -2.051543  11.676982   1.040469
[1]  46.373820 673.118761 570.780300  -2.259371  11.667689   1.041680


In [45]:
print(apply(etsclsminres,2,mean1))
print(apply(etsregminres,2,mean1))
print(apply(etsclsmeanres,2,mean1))
print(apply(etsregmeanres,2,mean1))

[1]  59.226247 674.239136 572.318787  -2.100347  11.674560   1.045695
[1]  59.5804019 682.5387496 579.0771889  -2.0027395  11.8611672   0.9721103
[1]  52.063383 674.098166 572.022089  -2.250658  11.710743   1.037606
[1]  40.6842580 682.0319945 578.2854161  -2.2680843  11.8075156   0.9824333


In [46]:
print(apply(etsrandomres[testindex,],2,mean))

[1]  50.589387 680.123321 576.760576  -2.216337  11.828061   1.130141


In [47]:
etsall=matrix(0,16,6)
etsall[1,]=apply(ets_pred_res[testindex,1,1,],2,mean1)[1:6]
etsall[2,]=apply(etsminxgbclsres,2,mean1)
etsall[3,]=apply(etsminxgbregres,2,mean1)
etsall[4,]=apply(etsminlgbclsres,2,mean1)
etsall[5,]=apply(etsminlgbregres,2,mean1)
etsall[6,]=apply(etsmeanxgbclsres,2,mean1)
etsall[7,]=apply(etsmeanxgbregres,2,mean1)
etsall[8,]=apply(etsmeanlgbclsres,2,mean1)
etsall[9,]=apply(etsmeanlgbregres,2,mean1)
etsall[10,]=apply(etsallminres,2,mean1)
etsall[11,]=apply(etsallmeanres,2,mean1)
etsall[12,]=apply(etsclsminres,2,mean1)
etsall[13,]=apply(etsregminres,2,mean1)
etsall[14,]=apply(etsclsmeanres,2,mean1)
etsall[15,]=apply(etsregmeanres,2,mean1)
etsall[16,]=apply(etsrandomres[testindex,],2,mean)

In [48]:
etsall

[,1]      [,2]     [,3]     [,4]      [,5]     [,6]     
 [1,]  9.762626 691.8408 586.8510 -3.008543 12.19538 1.1537802
 [2,] 63.325516 680.6060 578.5390 -2.175134 11.81564 0.9870874
 [3,] 65.572045 689.4227 585.7299 -1.984458 11.96244 0.9851388
 [4,] 55.126979 690.3721 586.1325 -2.025560 11.97961 1.1002783
 [5,] 53.588758 686.6011 582.3819 -2.021021 11.93580 0.9770844
 [6,] 53.446892 675.4017 571.8116 -2.268457 11.72869 0.9633273
 [7,] 45.244941 681.8850 578.1710 -2.312476 11.78420 0.9704909
 [8,] 50.679873 692.5577 588.7468 -2.232859 12.03424 1.1070105
 [9,] 36.123575 688.5118 584.2672 -2.223693 11.95526 0.9857779
[10,] 59.403325 673.6255 571.4880 -2.051543 11.67698 1.0404688
[11,] 46.373820 673.1188 570.7803 -2.259371 11.66769 1.0416801
[12,] 59.226247 674.2391 572.3188 -2.100347 11.67456 1.0456954
[13,] 59.580402 682.5387 579.0772 -2.002740 11.86117 0.9721103
[14,] 52.063383 674.0982 572.0221 -2.250658 11.71074 1.0376058
[15,] 40.684258 682.0320 578.2854 -2.268084 11.80752 0.9824333
[16,] 50.589387 680.1233 576.7606 -2.216337 11.82806 1.1301410

In [49]:
write.csv(etsall,'ets_Quarterly_final_res.csv')

## thetaf

### The error of each improved prediction result

In [50]:
start_time = Sys.time()

In [51]:
thetafxgbcls_min=meanpre(thetaf_predh,thetaf_pr_min[,1],h,testindex)
thetafxgbreg_min=meanpre(thetaf_predh,thetaf_pr_min[,2],h,testindex)
thetaflgbcls_min=meanpre(thetaf_predh,thetaf_pr_min[,3],h,testindex)
thetaflgbreg_min=meanpre(thetaf_predh,thetaf_pr_min[,4],h,testindex)

In [52]:
thetafxgbcls_mean=meanpre(thetaf_predh,thetaf_pr_mean[,1],h,testindex)
thetafxgbreg_mean=meanpre(thetaf_predh,thetaf_pr_mean[,2],h,testindex)
thetaflgbcls_mean=meanpre(thetaf_predh,thetaf_pr_mean[,3],h,testindex)
thetaflgbreg_mean=meanpre(thetaf_predh,thetaf_pr_mean[,4],h,testindex)

In [53]:
thetafminxgbclsres=predres(thetafxgbcls_min,data,thetaf_pr_min[,1],lengthtest,h,testindex)
thetafminxgbregres=predres(thetafxgbreg_min,data,thetaf_pr_min[,2],lengthtest,h,testindex)
thetafminlgbclsres=predres(thetaflgbcls_min,data,thetaf_pr_min[,3],lengthtest,h,testindex)
thetafminlgbregres=predres(thetaflgbreg_min,data,thetaf_pr_min[,4],lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

In [54]:
thetafmeanxgbclsres=predres(thetafxgbcls_mean,data,thetaf_pr_mean[,1],lengthtest,h,testindex)
thetafmeanxgbregres=predres(thetafxgbreg_mean,data,thetaf_pr_mean[,2],lengthtest,h,testindex)
thetafmeanlgbclsres=predres(thetaflgbcls_mean,data,thetaf_pr_mean[,3],lengthtest,h,testindex)
thetafmeanlgbregres=predres(thetaflgbreg_mean,data,thetaf_pr_mean[,4],lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

In [55]:
end_time = Sys.time()
time_matrix[3,]=end_time-start_time

In [56]:
end_time-start_time

Time difference of 4.185496 mins

### The results of the two methods of determining labels are averaged respectively

In [57]:
thetafallmin=(thetafxgbcls_min+thetaflgbcls_min+thetafxgbreg_min+thetaflgbreg_min)/4
thetafallmean=(thetafxgbcls_mean+thetaflgbcls_mean+thetafxgbreg_mean+thetaflgbreg_mean)/4

In [58]:
thetafallminres=predres_mul(thetafallmin,data,thetaf_pr_min,lengthtest,h,testindex)
thetafallmeanres=predres_mul(thetafallmean,data,thetaf_pr_mean,lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

### Under the above classification, the improved forecast results of the classification and regression models are averaged respectively

In [59]:
thetafclsmin=(thetafxgbcls_min+thetaflgbcls_min)/2
thetafregmin=(thetafxgbreg_min+thetaflgbreg_min)/2
thetafclsmean=(thetafxgbcls_mean+thetaflgbcls_mean)/2
thetafregmean=(thetafxgbreg_mean+thetaflgbreg_mean)/2

In [60]:
thetafclsminres=predres_mul(thetafclsmin,data,thetaf_pr_min[,c(1,3)],lengthtest,h,testindex)
thetafregminres=predres_mul(thetafregmin,data,thetaf_pr_min[,c(2,4)],lengthtest,h,testindex)
thetafclsmeanres=predres_mul(thetafclsmean,data,thetaf_pr_mean[,c(1,3)],lengthtest,h,testindex)
thetafregmeanres=predres_mul(thetafregmean,data,thetaf_pr_mean[,c(2,4)],lengthtest,h,testindex)

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

### Random slice

In [61]:
thetafpred_change<- aperm(thetaf_predh[1:datalength,1:m,1:n,1:h], c(1, 3, 2, 4))  
# 使用array函数将其转换为新的形状
thetafpred_change <- array(thetafpred_change, dim = c(datalength, m*n, h))

In [62]:
model=ets(data[[1]]$x)
fore_l=forecast(model,h=h)
thetafrandomres=matrix(0,datalength,6)
for (i in 1:datalength){
    random=sample(m*n,n)
    minloc=min(random)
    # 使用cut函数将数据分割为区间
    loc <- cut(minloc, breaks =seq(0,m*n,n), labels = FALSE)
    loc<-as.numeric(loc)
    thetafrandompred=apply(thetafpred_change[i,random,],2,mean)
    start=length5[i,loc]
    y_all=data[[i]]$x
    y=y_all[start:length(y_all)]
    fore_l$x=ts(y,frequency=freq,end=end(y_all))
    real=data[[i]]$xx
    fore_l$mean=ts(thetafrandompred,start=start(real),frequency=freq)
    res=accuracy(fore_l,real)
    thetafrandomres[i,]=res[2,1:6]
    }

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

...

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute

Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sampl

Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”
Warning message in .cbind.ts(list(e1, e2), c(deparse(substitute(e1))[1L], deparse(substitute(e2))[1L]), :
“non-intersecting series”
Warning message in trainingaccuracy(object, test, d, D):
“test elements must be within sample”


In [63]:
print(apply(thetaf_pred_res[testindex,1,1,],2,mean1))
print(apply(thetafminxgbclsres,2,mean1))
print(apply(thetafminxgbregres,2,mean1))
print(apply(thetafminlgbclsres,2,mean1))
print(apply(thetafminlgbregres,2,mean1))

[1]  82.005623 681.596876 580.781149  -2.013445  11.817821   1.223275
[1]  56.455354 694.701932 592.269023  -2.024883  12.106778   1.024002
[1]  57.950608 688.528667 586.977695  -2.034666  11.944485   1.014391
[1]  76.604573 689.286561 587.104339  -1.524481  12.115405   1.140850
[1]  68.425454 686.960384 585.987249  -1.751620  11.966908   1.003043


In [64]:
print(apply(thetafmeanxgbclsres,2,mean1))
print(apply(thetafmeanxgbregres,2,mean1))
print(apply(thetafmeanlgbclsres,2,mean1))
print(apply(thetafmeanlgbregres,2,mean1))

[1]  51.6594785 688.6531754 586.6407577  -2.0800128  11.9122854   0.9943951
[1]  60.629156 685.458374 584.530732  -1.974439  11.929712   1.010468
[1]  78.983644 690.385920 588.088503  -1.601236  12.028900   1.138212
[1]  61.638057 683.149375 582.687110  -1.908295  11.881163   1.003796


In [65]:
print(apply(thetafallminres,2,mean1))
print(apply(thetafallmeanres,2,mean1))

[1]  64.858997 679.588360 579.065407  -1.833913  11.814840   1.078259
[1]  63.227584 678.399847 578.005055  -1.890995  11.757024   1.076517


In [66]:
print(apply(thetafallminres,2,mean1))
print(apply(thetafallmeanres,2,mean1))

[1]  64.858997 679.588360 579.065407  -1.833913  11.814840   1.078259
[1]  63.227584 678.399847 578.005055  -1.890995  11.757024   1.076517


In [67]:
print(apply(thetafclsminres,2,mean1))
print(apply(thetafclsmeanres,2,mean1))
print(apply(thetafregminres,2,mean1))
print(apply(thetafregmeanres,2,mean1))

[1]  66.529964 682.432743 581.252641  -1.774682  11.900442   1.087051
[1]  65.321561 681.055791 579.927393  -1.840624  11.807761   1.072802
[1]  63.188031 684.593634 583.820904  -1.893143  11.883520   1.004070
[1]  61.133607 682.321588 581.997128  -1.941367  11.873127   1.012953


In [68]:
print(apply(thetafrandomres[testindex,],2,mean1))

[1]  75.782179 683.900035 582.961302  -1.679009  11.844457   1.178272


In [69]:
thetafall=matrix(0,16,6)
thetafall[1,]=apply(thetaf_pred_res[testindex,1,1,],2,mean1)[1:6]
thetafall[2,]=apply(thetafminxgbclsres,2,mean1)
thetafall[3,]=apply(thetafminxgbregres,2,mean1)
thetafall[4,]=apply(thetafminlgbclsres,2,mean1)
thetafall[5,]=apply(thetafminlgbregres,2,mean1)
thetafall[6,]=apply(thetafmeanxgbclsres,2,mean1)
thetafall[7,]=apply(thetafmeanxgbregres,2,mean1)
thetafall[8,]=apply(thetafmeanlgbclsres,2,mean1)
thetafall[9,]=apply(thetafmeanlgbregres,2,mean1)
thetafall[10,]=apply(thetafallminres,2,mean1)
thetafall[11,]=apply(thetafallmeanres,2,mean1)
thetafall[12,]=apply(thetafclsminres,2,mean1)
thetafall[13,]=apply(thetafclsmeanres,2,mean1)
thetafall[14,]=apply(thetafregminres,2,mean1)
thetafall[15,]=apply(thetafregmeanres,2,mean1)
thetafall[16,]=apply(thetafrandomres[testindex,],2,mean1)

In [70]:
thetafall

[,1]     [,2]     [,3]     [,4]      [,5]     [,6]     
 [1,] 82.00562 681.5969 580.7811 -2.013445 11.81782 1.2232748
 [2,] 56.45535 694.7019 592.2690 -2.024883 12.10678 1.0240017
 [3,] 57.95061 688.5287 586.9777 -2.034666 11.94448 1.0143915
 [4,] 76.60457 689.2866 587.1043 -1.524481 12.11541 1.1408501
 [5,] 68.42545 686.9604 585.9872 -1.751620 11.96691 1.0030425
 [6,] 51.65948 688.6532 586.6408 -2.080013 11.91229 0.9943951
 [7,] 60.62916 685.4584 584.5307 -1.974439 11.92971 1.0104676
 [8,] 78.98364 690.3859 588.0885 -1.601236 12.02890 1.1382120
 [9,] 61.63806 683.1494 582.6871 -1.908295 11.88116 1.0037965
[10,] 64.85900 679.5884 579.0654 -1.833913 11.81484 1.0782594
[11,] 63.22758 678.3998 578.0051 -1.890995 11.75702 1.0765172
[12,] 66.52996 682.4327 581.2526 -1.774682 11.90044 1.0870509
[13,] 65.32156 681.0558 579.9274 -1.840624 11.80776 1.0728024
[14,] 63.18803 684.5936 583.8209 -1.893143 11.88352 1.0040701
[15,] 61.13361 682.3216 581.9971 -1.941367 11.87313 1.0129532
[16,] 75.78218 683.9000 582.9613 -1.679009 11.84446 1.1782719

In [71]:
write.csv(thetafall,'thetaf_Quarterly_final_res.csv')

In [72]:
time_matrix

user_time system_time elapsed_time
[1,] 1.449380  1.449380    1.449380    
[2,] 3.140769  3.140769    3.140769    
[3,] 4.185496  4.185496    4.185496

In [73]:
write.csv(time_matrix,'Quarterly_time_matrix.csv')